In [1]:
import pandas as pd
import scipy.stats as stats

from sklearn import metrics, model_selection
from catboost import CatBoostClassifier

In [2]:
df_train = pd.read_csv('../../Feature_Encoding/data/train_count_encoding.csv')
df_test = pd.read_csv('../../Feature_Encoding/data/test_count_encoding.csv')
train = pd.read_csv('../../Feature_Engineering/data/other-cleaned_train.csv')

In [3]:
def cross_val(model, x_train, y_train):
    score_cross_val = model_selection.cross_val_score(model, x_train, y_train, cv=5)
    print(score_cross_val.mean())

In [4]:
#Realiza busqueda completa combinando los parametros
def catboost(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb = {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.05, 0.1], 'l2_leaf_reg': [0, 1, 5]}    
    catb_gs = model_selection.GridSearchCV(catb_classifier, params_catb, cv=5)
    catb_gs.fit(x_train, y_train)
    catb_best = catb_gs.best_estimator_
    print(catb_gs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [5]:
#Realiza busqueda random dentro de los parametros validos
def catboost2(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb_2={
        'n_estimators':stats.randint(10,500),'learning_rate':stats.uniform(0.01,0.3),
        'subsample':stats.uniform(0.3,0.7),'l2_leaf_reg':[1,5,10],
        'max_depth':[3,10,6],'colsample_bylevel':stats.uniform(0.,0.6)
    }
    
    catb_rs = model_selection.RandomizedSearchCV(CatBoostClassifier(),
                          param_distributions=params_catb_2,
                          cv=2,
                          scoring='neg_log_loss',
                          verbose=1,
                          n_iter=200)
    
    catb_rs.fit(x_train, y_train)
    catb_best = catb_rs.best_estimator_
    print(catb_rs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [6]:
def test_model(model, x_test, y_test):
    predictions = model.predict_proba(x_test)[:,1]
    logloss = metrics.log_loss(y_test, predictions)
    accuracy = metrics.accuracy_score(y_test, predictions.round())
    print("Accuracy: %.2f%%, Logloss: %.2f" % (accuracy*100.0, logloss))

In [7]:
y = train.Target
x_train, x_validation, y_train, y_validation = model_selection.train_test_split(df_train, y, test_size=0.3, stratify=y)

In [8]:
catboost_c = catboost(x_train, y_train, x_validation, y_validation)
test_model(catboost_c, x_validation, y_validation)
cross_val(catboost_c, x_train, y_train)

0:	learn: 0.6847141	total: 78.8ms	remaining: 3.86s
1:	learn: 0.6758855	total: 86ms	remaining: 2.06s
2:	learn: 0.6671572	total: 93.2ms	remaining: 1.46s
3:	learn: 0.6585906	total: 100ms	remaining: 1.16s
4:	learn: 0.6508168	total: 107ms	remaining: 964ms
5:	learn: 0.6436852	total: 114ms	remaining: 839ms
6:	learn: 0.6379976	total: 122ms	remaining: 749ms
7:	learn: 0.6307936	total: 129ms	remaining: 676ms
8:	learn: 0.6229665	total: 136ms	remaining: 619ms
9:	learn: 0.6156658	total: 145ms	remaining: 581ms
10:	learn: 0.6082022	total: 153ms	remaining: 541ms
11:	learn: 0.6023019	total: 160ms	remaining: 506ms
12:	learn: 0.5968514	total: 167ms	remaining: 476ms
13:	learn: 0.5913837	total: 175ms	remaining: 450ms
14:	learn: 0.5866106	total: 184ms	remaining: 428ms
15:	learn: 0.5817234	total: 195ms	remaining: 414ms
16:	learn: 0.5754383	total: 204ms	remaining: 395ms
17:	learn: 0.5706200	total: 211ms	remaining: 376ms
18:	learn: 0.5659960	total: 219ms	remaining: 357ms
19:	learn: 0.5611663	total: 229ms	remain

22:	learn: 0.5474464	total: 210ms	remaining: 247ms
23:	learn: 0.5428088	total: 219ms	remaining: 237ms
24:	learn: 0.5391503	total: 227ms	remaining: 227ms
25:	learn: 0.5346284	total: 235ms	remaining: 217ms
26:	learn: 0.5309907	total: 252ms	remaining: 215ms
27:	learn: 0.5267562	total: 260ms	remaining: 204ms
28:	learn: 0.5235798	total: 273ms	remaining: 198ms
29:	learn: 0.5197296	total: 282ms	remaining: 188ms
30:	learn: 0.5162547	total: 290ms	remaining: 178ms
31:	learn: 0.5127421	total: 310ms	remaining: 174ms
32:	learn: 0.5087093	total: 321ms	remaining: 165ms
33:	learn: 0.5053161	total: 334ms	remaining: 157ms
34:	learn: 0.5022631	total: 343ms	remaining: 147ms
35:	learn: 0.4996534	total: 361ms	remaining: 140ms
36:	learn: 0.4965988	total: 370ms	remaining: 130ms
37:	learn: 0.4939168	total: 377ms	remaining: 119ms
38:	learn: 0.4909342	total: 384ms	remaining: 108ms
39:	learn: 0.4873888	total: 393ms	remaining: 98.2ms
40:	learn: 0.4841973	total: 402ms	remaining: 88.3ms
41:	learn: 0.4815555	total: 4

90:	learn: 0.3984859	total: 1s	remaining: 99ms
91:	learn: 0.3971800	total: 1.01s	remaining: 87.7ms
92:	learn: 0.3958022	total: 1.02s	remaining: 76.6ms
93:	learn: 0.3948433	total: 1.02s	remaining: 65.4ms
94:	learn: 0.3939826	total: 1.03s	remaining: 54.3ms
95:	learn: 0.3928079	total: 1.04s	remaining: 43.3ms
96:	learn: 0.3919011	total: 1.05s	remaining: 32.4ms
97:	learn: 0.3907802	total: 1.05s	remaining: 21.5ms
98:	learn: 0.3899743	total: 1.06s	remaining: 10.7ms
99:	learn: 0.3889929	total: 1.07s	remaining: 0us
0:	learn: 0.6845325	total: 8.12ms	remaining: 804ms
1:	learn: 0.6776557	total: 15.1ms	remaining: 737ms
2:	learn: 0.6685645	total: 23.4ms	remaining: 756ms
3:	learn: 0.6603000	total: 30.7ms	remaining: 737ms
4:	learn: 0.6523450	total: 38.1ms	remaining: 724ms
5:	learn: 0.6450892	total: 45.2ms	remaining: 708ms
6:	learn: 0.6392600	total: 52.6ms	remaining: 699ms
7:	learn: 0.6318815	total: 65.3ms	remaining: 751ms
8:	learn: 0.6238172	total: 73ms	remaining: 738ms
9:	learn: 0.6147177	total: 80.6

75:	learn: 0.4147590	total: 606ms	remaining: 191ms
76:	learn: 0.4135467	total: 615ms	remaining: 184ms
77:	learn: 0.4121202	total: 623ms	remaining: 176ms
78:	learn: 0.4108961	total: 631ms	remaining: 168ms
79:	learn: 0.4096895	total: 640ms	remaining: 160ms
80:	learn: 0.4087190	total: 648ms	remaining: 152ms
81:	learn: 0.4075598	total: 657ms	remaining: 144ms
82:	learn: 0.4062060	total: 666ms	remaining: 136ms
83:	learn: 0.4052383	total: 674ms	remaining: 128ms
84:	learn: 0.4035957	total: 682ms	remaining: 120ms
85:	learn: 0.4023974	total: 690ms	remaining: 112ms
86:	learn: 0.4010544	total: 697ms	remaining: 104ms
87:	learn: 0.3999832	total: 706ms	remaining: 96.3ms
88:	learn: 0.3988780	total: 713ms	remaining: 88.2ms
89:	learn: 0.3976711	total: 722ms	remaining: 80.2ms
90:	learn: 0.3966107	total: 730ms	remaining: 72.2ms
91:	learn: 0.3951975	total: 738ms	remaining: 64.2ms
92:	learn: 0.3941540	total: 747ms	remaining: 56.2ms
93:	learn: 0.3932275	total: 755ms	remaining: 48.2ms
94:	learn: 0.3921315	tot

36:	learn: 0.4960366	total: 420ms	remaining: 716ms
37:	learn: 0.4928715	total: 429ms	remaining: 699ms
38:	learn: 0.4900460	total: 437ms	remaining: 684ms
39:	learn: 0.4866324	total: 447ms	remaining: 670ms
40:	learn: 0.4836350	total: 455ms	remaining: 655ms
41:	learn: 0.4806924	total: 463ms	remaining: 640ms
42:	learn: 0.4781471	total: 471ms	remaining: 625ms
43:	learn: 0.4757679	total: 485ms	remaining: 617ms
44:	learn: 0.4731847	total: 493ms	remaining: 603ms
45:	learn: 0.4705705	total: 501ms	remaining: 589ms
46:	learn: 0.4681288	total: 509ms	remaining: 574ms
47:	learn: 0.4662161	total: 518ms	remaining: 561ms
48:	learn: 0.4640822	total: 526ms	remaining: 547ms
49:	learn: 0.4619752	total: 535ms	remaining: 535ms
50:	learn: 0.4595240	total: 543ms	remaining: 522ms
51:	learn: 0.4579883	total: 552ms	remaining: 509ms
52:	learn: 0.4554762	total: 560ms	remaining: 497ms
53:	learn: 0.4535108	total: 568ms	remaining: 484ms
54:	learn: 0.4515957	total: 577ms	remaining: 472ms
55:	learn: 0.4496546	total: 585

...

23:	learn: 0.3187019	total: 212ms	remaining: 1.55s
24:	learn: 0.3159423	total: 227ms	remaining: 1.59s
25:	learn: 0.3128902	total: 241ms	remaining: 1.61s
26:	learn: 0.3101779	total: 256ms	remaining: 1.64s
27:	learn: 0.3071625	total: 279ms	remaining: 1.71s
28:	learn: 0.3044950	total: 295ms	remaining: 1.74s
29:	learn: 0.3023110	total: 311ms	remaining: 1.76s
30:	learn: 0.2997634	total: 336ms	remaining: 1.83s
31:	learn: 0.2973723	total: 355ms	remaining: 1.86s
32:	learn: 0.2948796	total: 367ms	remaining: 1.86s
33:	learn: 0.2919487	total: 391ms	remaining: 1.91s
34:	learn: 0.2890400	total: 408ms	remaining: 1.92s
35:	learn: 0.2861917	total: 427ms	remaining: 1.94s
36:	learn: 0.2842292	total: 444ms	remaining: 1.96s
37:	learn: 0.2824257	total: 461ms	remaining: 1.97s
38:	learn: 0.2811368	total: 476ms	remaining: 1.97s
39:	learn: 0.2799322	total: 492ms	remaining: 1.97s
40:	learn: 0.2775930	total: 509ms	remaining: 1.97s
41:	learn: 0.2763857	total: 528ms	remaining: 1.99s
42:	learn: 0.2743419	total: 541

184:	learn: 0.1275203	total: 2.03s	remaining: 165ms
185:	learn: 0.1266129	total: 2.05s	remaining: 154ms
186:	learn: 0.1261599	total: 2.06s	remaining: 143ms
187:	learn: 0.1256996	total: 2.07s	remaining: 132ms
188:	learn: 0.1251180	total: 2.1s	remaining: 122ms
189:	learn: 0.1243133	total: 2.11s	remaining: 111ms
190:	learn: 0.1236879	total: 2.12s	remaining: 100ms
191:	learn: 0.1230651	total: 2.13s	remaining: 88.9ms
192:	learn: 0.1223192	total: 2.14s	remaining: 77.7ms
193:	learn: 0.1215245	total: 2.15s	remaining: 66.6ms
194:	learn: 0.1210100	total: 2.16s	remaining: 55.5ms
195:	learn: 0.1204496	total: 2.17s	remaining: 44.3ms
196:	learn: 0.1197444	total: 2.18s	remaining: 33.2ms
197:	learn: 0.1192360	total: 2.19s	remaining: 22.1ms
198:	learn: 0.1185845	total: 2.2s	remaining: 11.1ms
199:	learn: 0.1180448	total: 2.21s	remaining: 0us
0:	learn: 0.6187217	total: 20.4ms	remaining: 4.05s
1:	learn: 0.5624136	total: 35ms	remaining: 3.47s
2:	learn: 0.5155947	total: 46.6ms	remaining: 3.06s
3:	learn: 0.4

157:	learn: 0.1374594	total: 1.65s	remaining: 439ms
158:	learn: 0.1369763	total: 1.66s	remaining: 428ms
159:	learn: 0.1365339	total: 1.67s	remaining: 417ms
160:	learn: 0.1359105	total: 1.68s	remaining: 406ms
161:	learn: 0.1353462	total: 1.69s	remaining: 396ms
162:	learn: 0.1346781	total: 1.69s	remaining: 385ms
163:	learn: 0.1337895	total: 1.7s	remaining: 374ms
164:	learn: 0.1330098	total: 1.71s	remaining: 363ms
165:	learn: 0.1323663	total: 1.72s	remaining: 352ms
166:	learn: 0.1313901	total: 1.73s	remaining: 341ms
167:	learn: 0.1303052	total: 1.74s	remaining: 331ms
168:	learn: 0.1296923	total: 1.74s	remaining: 320ms
169:	learn: 0.1290818	total: 1.76s	remaining: 311ms
170:	learn: 0.1283091	total: 1.77s	remaining: 300ms
171:	learn: 0.1277244	total: 1.78s	remaining: 289ms
172:	learn: 0.1270741	total: 1.78s	remaining: 279ms
173:	learn: 0.1264638	total: 1.79s	remaining: 268ms
174:	learn: 0.1257508	total: 1.8s	remaining: 258ms
175:	learn: 0.1250955	total: 1.81s	remaining: 247ms
176:	learn: 0.

128:	learn: 0.1577762	total: 1.23s	remaining: 678ms
129:	learn: 0.1570127	total: 1.25s	remaining: 673ms
130:	learn: 0.1560055	total: 1.26s	remaining: 664ms
131:	learn: 0.1549699	total: 1.27s	remaining: 654ms
132:	learn: 0.1543735	total: 1.28s	remaining: 645ms
133:	learn: 0.1535637	total: 1.29s	remaining: 635ms
134:	learn: 0.1528426	total: 1.31s	remaining: 632ms
135:	learn: 0.1521191	total: 1.33s	remaining: 625ms
136:	learn: 0.1512190	total: 1.36s	remaining: 628ms
137:	learn: 0.1503013	total: 1.39s	remaining: 622ms
138:	learn: 0.1492892	total: 1.4s	remaining: 614ms
139:	learn: 0.1484342	total: 1.42s	remaining: 609ms
140:	learn: 0.1478954	total: 1.43s	remaining: 599ms
141:	learn: 0.1469527	total: 1.44s	remaining: 589ms
142:	learn: 0.1460543	total: 1.45s	remaining: 579ms
143:	learn: 0.1456465	total: 1.46s	remaining: 568ms
144:	learn: 0.1447995	total: 1.47s	remaining: 558ms
145:	learn: 0.1442996	total: 1.48s	remaining: 547ms
146:	learn: 0.1437000	total: 1.49s	remaining: 536ms
147:	learn: 0

109:	learn: 0.1782426	total: 1.03s	remaining: 841ms
110:	learn: 0.1771166	total: 1.04s	remaining: 832ms
111:	learn: 0.1756794	total: 1.05s	remaining: 822ms
112:	learn: 0.1745153	total: 1.06s	remaining: 818ms
113:	learn: 0.1731597	total: 1.08s	remaining: 813ms
114:	learn: 0.1721226	total: 1.09s	remaining: 803ms
115:	learn: 0.1709670	total: 1.1s	remaining: 794ms
116:	learn: 0.1700515	total: 1.11s	remaining: 785ms
117:	learn: 0.1693372	total: 1.12s	remaining: 776ms
118:	learn: 0.1683782	total: 1.13s	remaining: 767ms
119:	learn: 0.1674655	total: 1.14s	remaining: 757ms
120:	learn: 0.1661923	total: 1.15s	remaining: 748ms
121:	learn: 0.1654995	total: 1.16s	remaining: 741ms
122:	learn: 0.1644264	total: 1.17s	remaining: 733ms
123:	learn: 0.1636892	total: 1.19s	remaining: 729ms
124:	learn: 0.1627200	total: 1.2s	remaining: 720ms
125:	learn: 0.1618760	total: 1.21s	remaining: 712ms
126:	learn: 0.1609565	total: 1.22s	remaining: 703ms
127:	learn: 0.1596552	total: 1.23s	remaining: 694ms
128:	learn: 0.

In [9]:
catboost_2 = catboost2(x_train, y_train, x_validation, y_validation)
test_model(catboost_2, x_validation, y_validation)
cross_val(catboost_2, x_train, y_train)

Fitting 2 folds for each of 200 candidates, totalling 400 fits
0:	learn: 0.5461438	total: 15.9ms	remaining: 1.27s
1:	learn: 0.4648396	total: 33.2ms	remaining: 1.31s
2:	learn: 0.4246216	total: 47.1ms	remaining: 1.22s
3:	learn: 0.3954590	total: 62.9ms	remaining: 1.21s
4:	learn: 0.3786511	total: 73.2ms	remaining: 1.11s
5:	learn: 0.3625672	total: 88ms	remaining: 1.1s
6:	learn: 0.3543138	total: 104ms	remaining: 1.1s
7:	learn: 0.3421401	total: 116ms	remaining: 1.06s
8:	learn: 0.3373884	total: 129ms	remaining: 1.03s
9:	learn: 0.3339562	total: 140ms	remaining: 997ms
10:	learn: 0.3272647	total: 153ms	remaining: 976ms
11:	learn: 0.3212673	total: 163ms	remaining: 938ms
12:	learn: 0.3163080	total: 172ms	remaining: 900ms
13:	learn: 0.3088084	total: 180ms	remaining: 862ms
14:	learn: 0.3023523	total: 188ms	remaining: 829ms
15:	learn: 0.2984713	total: 198ms	remaining: 804ms
16:	learn: 0.2948381	total: 207ms	remaining: 780ms
17:	learn: 0.2913150	total: 215ms	remaining: 753ms
18:	learn: 0.2881814	total:

0:	learn: 0.5516784	total: 5.38ms	remaining: 1.16s
1:	learn: 0.4776419	total: 11.1ms	remaining: 1.19s
2:	learn: 0.4366590	total: 16.3ms	remaining: 1.16s
3:	learn: 0.4076045	total: 21.3ms	remaining: 1.13s
4:	learn: 0.3876146	total: 27ms	remaining: 1.14s
5:	learn: 0.3705777	total: 32.3ms	remaining: 1.13s
6:	learn: 0.3552241	total: 37.5ms	remaining: 1.12s
7:	learn: 0.3484220	total: 42.4ms	remaining: 1.1s
8:	learn: 0.3440578	total: 47.6ms	remaining: 1.09s
9:	learn: 0.3384321	total: 52.8ms	remaining: 1.09s
10:	learn: 0.3341808	total: 57.5ms	remaining: 1.07s
11:	learn: 0.3297584	total: 65.4ms	remaining: 1.11s
12:	learn: 0.3226010	total: 72.1ms	remaining: 1.13s
13:	learn: 0.3174293	total: 85.9ms	remaining: 1.24s
14:	learn: 0.3099204	total: 121ms	remaining: 1.62s
15:	learn: 0.3070541	total: 146ms	remaining: 1.82s
16:	learn: 0.3040296	total: 166ms	remaining: 1.94s
17:	learn: 0.3019124	total: 190ms	remaining: 2.09s
18:	learn: 0.2979396	total: 209ms	remaining: 2.17s
19:	learn: 0.2951740	total: 22

173:	learn: 0.0808037	total: 1.56s	remaining: 376ms
174:	learn: 0.0803452	total: 1.56s	remaining: 366ms
175:	learn: 0.0799258	total: 1.57s	remaining: 357ms
176:	learn: 0.0791343	total: 1.58s	remaining: 347ms
177:	learn: 0.0784239	total: 1.58s	remaining: 338ms
178:	learn: 0.0783455	total: 1.59s	remaining: 328ms
179:	learn: 0.0780354	total: 1.59s	remaining: 319ms
180:	learn: 0.0776109	total: 1.6s	remaining: 310ms
181:	learn: 0.0772808	total: 1.61s	remaining: 300ms
182:	learn: 0.0769897	total: 1.61s	remaining: 291ms
183:	learn: 0.0765846	total: 1.62s	remaining: 282ms
184:	learn: 0.0763246	total: 1.63s	remaining: 273ms
185:	learn: 0.0760524	total: 1.63s	remaining: 263ms
186:	learn: 0.0751812	total: 1.64s	remaining: 254ms
187:	learn: 0.0749201	total: 1.64s	remaining: 245ms
188:	learn: 0.0743824	total: 1.65s	remaining: 236ms
189:	learn: 0.0739025	total: 1.66s	remaining: 227ms
190:	learn: 0.0737038	total: 1.66s	remaining: 217ms
191:	learn: 0.0731771	total: 1.67s	remaining: 208ms
192:	learn: 0

122:	learn: 0.1094879	total: 816ms	remaining: 617ms
123:	learn: 0.1080066	total: 822ms	remaining: 610ms
124:	learn: 0.1069497	total: 828ms	remaining: 603ms
125:	learn: 0.1065269	total: 834ms	remaining: 595ms
126:	learn: 0.1057247	total: 840ms	remaining: 588ms
127:	learn: 0.1049121	total: 845ms	remaining: 581ms
128:	learn: 0.1039800	total: 851ms	remaining: 574ms
129:	learn: 0.1030759	total: 856ms	remaining: 566ms
130:	learn: 0.1019374	total: 862ms	remaining: 559ms
131:	learn: 0.1010054	total: 868ms	remaining: 553ms
132:	learn: 0.1003904	total: 874ms	remaining: 545ms
133:	learn: 0.0999602	total: 880ms	remaining: 538ms
134:	learn: 0.0998679	total: 885ms	remaining: 531ms
135:	learn: 0.0990368	total: 890ms	remaining: 524ms
136:	learn: 0.0984143	total: 896ms	remaining: 516ms
137:	learn: 0.0973659	total: 901ms	remaining: 509ms
138:	learn: 0.0965789	total: 907ms	remaining: 502ms
139:	learn: 0.0955984	total: 913ms	remaining: 495ms
140:	learn: 0.0952079	total: 919ms	remaining: 489ms
141:	learn: 

105:	learn: 0.2683440	total: 400ms	remaining: 973ms
106:	learn: 0.2683076	total: 403ms	remaining: 969ms
107:	learn: 0.2678406	total: 406ms	remaining: 962ms
108:	learn: 0.2663123	total: 410ms	remaining: 958ms
109:	learn: 0.2662966	total: 414ms	remaining: 955ms
110:	learn: 0.2638266	total: 419ms	remaining: 955ms
111:	learn: 0.2628845	total: 424ms	remaining: 954ms
112:	learn: 0.2620665	total: 428ms	remaining: 951ms
113:	learn: 0.2617518	total: 431ms	remaining: 946ms
114:	learn: 0.2612839	total: 434ms	remaining: 940ms
115:	learn: 0.2602143	total: 440ms	remaining: 940ms
116:	learn: 0.2601759	total: 442ms	remaining: 933ms
117:	learn: 0.2582306	total: 446ms	remaining: 931ms
118:	learn: 0.2582306	total: 448ms	remaining: 923ms
119:	learn: 0.2580593	total: 452ms	remaining: 919ms
120:	learn: 0.2580593	total: 453ms	remaining: 911ms
121:	learn: 0.2580511	total: 457ms	remaining: 906ms
122:	learn: 0.2580089	total: 459ms	remaining: 900ms
123:	learn: 0.2563969	total: 463ms	remaining: 897ms
124:	learn: 

...

255:	learn: 0.0926804	total: 6.38s	remaining: 6s
256:	learn: 0.0923357	total: 6.4s	remaining: 5.97s
257:	learn: 0.0920569	total: 6.42s	remaining: 5.95s
258:	learn: 0.0915649	total: 6.45s	remaining: 5.92s
259:	learn: 0.0913260	total: 6.47s	remaining: 5.9s
260:	learn: 0.0910904	total: 6.5s	remaining: 5.87s
261:	learn: 0.0906261	total: 6.52s	remaining: 5.85s
262:	learn: 0.0902943	total: 6.54s	remaining: 5.82s
263:	learn: 0.0898951	total: 6.57s	remaining: 5.79s
264:	learn: 0.0895119	total: 6.59s	remaining: 5.77s
265:	learn: 0.0891554	total: 6.62s	remaining: 5.74s
266:	learn: 0.0889763	total: 6.64s	remaining: 5.72s
267:	learn: 0.0887569	total: 6.66s	remaining: 5.69s
268:	learn: 0.0882920	total: 6.69s	remaining: 5.67s
269:	learn: 0.0880851	total: 6.71s	remaining: 5.64s
270:	learn: 0.0876695	total: 6.74s	remaining: 5.62s
271:	learn: 0.0872974	total: 6.76s	remaining: 5.59s
272:	learn: 0.0868379	total: 6.78s	remaining: 5.57s
273:	learn: 0.0865046	total: 6.81s	remaining: 5.54s
274:	learn: 0.0862

422:	learn: 0.0531520	total: 10.4s	remaining: 1.83s
423:	learn: 0.0529321	total: 10.5s	remaining: 1.8s
424:	learn: 0.0527777	total: 10.5s	remaining: 1.78s
425:	learn: 0.0525349	total: 10.5s	remaining: 1.75s
426:	learn: 0.0522755	total: 10.5s	remaining: 1.73s
427:	learn: 0.0521208	total: 10.6s	remaining: 1.7s
428:	learn: 0.0519251	total: 10.6s	remaining: 1.68s
429:	learn: 0.0516938	total: 10.6s	remaining: 1.65s
430:	learn: 0.0515645	total: 10.6s	remaining: 1.63s
431:	learn: 0.0514009	total: 10.7s	remaining: 1.6s
432:	learn: 0.0513224	total: 10.7s	remaining: 1.58s
433:	learn: 0.0511658	total: 10.7s	remaining: 1.55s
434:	learn: 0.0510084	total: 10.7s	remaining: 1.53s
435:	learn: 0.0508352	total: 10.8s	remaining: 1.5s
436:	learn: 0.0507112	total: 10.8s	remaining: 1.48s
437:	learn: 0.0505960	total: 10.8s	remaining: 1.45s
438:	learn: 0.0505454	total: 10.8s	remaining: 1.43s
439:	learn: 0.0504595	total: 10.8s	remaining: 1.4s
440:	learn: 0.0503152	total: 10.9s	remaining: 1.38s
441:	learn: 0.050

88:	learn: 0.1960979	total: 2.14s	remaining: 9.83s
89:	learn: 0.1953715	total: 2.17s	remaining: 9.79s
90:	learn: 0.1940525	total: 2.19s	remaining: 9.77s
91:	learn: 0.1924632	total: 2.21s	remaining: 9.74s
92:	learn: 0.1915150	total: 2.24s	remaining: 9.73s
93:	learn: 0.1907194	total: 2.26s	remaining: 9.71s
94:	learn: 0.1896460	total: 2.29s	remaining: 9.7s
95:	learn: 0.1892143	total: 2.31s	remaining: 9.67s
96:	learn: 0.1879434	total: 2.33s	remaining: 9.63s
97:	learn: 0.1868706	total: 2.36s	remaining: 9.6s
98:	learn: 0.1863261	total: 2.38s	remaining: 9.57s
99:	learn: 0.1853929	total: 2.4s	remaining: 9.54s
100:	learn: 0.1843011	total: 2.42s	remaining: 9.49s
101:	learn: 0.1827957	total: 2.45s	remaining: 9.48s
102:	learn: 0.1815123	total: 2.47s	remaining: 9.44s
103:	learn: 0.1804620	total: 2.49s	remaining: 9.41s
104:	learn: 0.1789661	total: 2.52s	remaining: 9.4s
105:	learn: 0.1779088	total: 2.55s	remaining: 9.39s
106:	learn: 0.1760968	total: 2.57s	remaining: 9.37s
107:	learn: 0.1751827	total:

251:	learn: 0.0930786	total: 6.43s	remaining: 6.25s
252:	learn: 0.0928671	total: 6.45s	remaining: 6.22s
253:	learn: 0.0925200	total: 6.48s	remaining: 6.2s
254:	learn: 0.0922684	total: 6.5s	remaining: 6.17s
255:	learn: 0.0919865	total: 6.53s	remaining: 6.14s
256:	learn: 0.0917763	total: 6.55s	remaining: 6.12s
257:	learn: 0.0914507	total: 6.57s	remaining: 6.09s
258:	learn: 0.0911628	total: 6.59s	remaining: 6.06s
259:	learn: 0.0909053	total: 6.62s	remaining: 6.03s
260:	learn: 0.0906253	total: 6.64s	remaining: 6.01s
261:	learn: 0.0903851	total: 6.67s	remaining: 5.98s
262:	learn: 0.0901408	total: 6.7s	remaining: 5.96s
263:	learn: 0.0898725	total: 6.72s	remaining: 5.93s
264:	learn: 0.0894213	total: 6.74s	remaining: 5.9s
265:	learn: 0.0892299	total: 6.77s	remaining: 5.88s
266:	learn: 0.0890649	total: 6.79s	remaining: 5.85s
267:	learn: 0.0884656	total: 6.81s	remaining: 5.82s
268:	learn: 0.0881539	total: 6.84s	remaining: 5.79s
269:	learn: 0.0877815	total: 6.86s	remaining: 5.77s
270:	learn: 0.08

412:	learn: 0.0544478	total: 10.3s	remaining: 2.1s
413:	learn: 0.0542792	total: 10.3s	remaining: 2.07s
414:	learn: 0.0540739	total: 10.4s	remaining: 2.05s
415:	learn: 0.0539389	total: 10.4s	remaining: 2.02s
416:	learn: 0.0537984	total: 10.4s	remaining: 2s
417:	learn: 0.0537112	total: 10.4s	remaining: 1.97s
418:	learn: 0.0535938	total: 10.5s	remaining: 1.95s
419:	learn: 0.0534681	total: 10.5s	remaining: 1.92s
420:	learn: 0.0533543	total: 10.5s	remaining: 1.9s
421:	learn: 0.0532287	total: 10.5s	remaining: 1.87s
422:	learn: 0.0530106	total: 10.6s	remaining: 1.85s
423:	learn: 0.0528606	total: 10.6s	remaining: 1.82s
424:	learn: 0.0526978	total: 10.6s	remaining: 1.8s
425:	learn: 0.0525264	total: 10.6s	remaining: 1.77s
426:	learn: 0.0523603	total: 10.7s	remaining: 1.75s
427:	learn: 0.0521572	total: 10.7s	remaining: 1.72s
428:	learn: 0.0520020	total: 10.7s	remaining: 1.7s
429:	learn: 0.0518587	total: 10.7s	remaining: 1.67s
430:	learn: 0.0517343	total: 10.8s	remaining: 1.65s
431:	learn: 0.05156

In [10]:
y_pred = catboost_2.predict_proba(df_test)[:,1]
submission_catboost = pd.DataFrame(data={'Opportunity_ID':df_test['Opportunity_ID'], 'Target': y_pred})
submission_catboost = submission_catboost.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_catboost.to_csv('../submits/count_catboost.csv', index=False)